In [2]:
from sklearn import preprocessing,tree,metrics
from sklearn.model_selection import train_test_split,GridSearchCV
from matplotlib import pyplot as plt
from sklearn.tree import DecisionTreeClassifier,DecisionTreeRegressor
from sklearn.metrics import accuracy_score,classification_report,confusion_matrix,ConfusionMatrixDisplay,RocCurveDisplay
import pandas as pd 
import numpy as np 
import plotly.express as px 

In [3]:
pd.set_option('display.max_rows',3000)
pd.set_option('display.max_columns',3000)
pd.set_option('display.width',150)
pd.set_option('display.float_format','{:.2f}'.format)

In [4]:
data = pd.read_csv('loan_approval_data.csv')

In [5]:
data.shape

(58645, 13)

In [6]:
data.head()

id   age  income home_ownership  emplyment_length      loan_intent  loan_amount  loan_interest_rate  loan_income_ratio  \
0  35437 21.00   12000            OWN                 0        EDUCATION        15000                6.99               0.12   
1  53756 21.00   13200            OWN                 2        EDUCATION        25000               16.77               0.19   
2  42205 23.00    9600           RENT                 5          MEDICAL        30000               12.42               0.31   
3  19180 40.00  182004           RENT                 3        EDUCATION        35000                8.00               0.19   
4  28072 40.00   90000       MORTGAGE                 3  HOMEIMPROVEMENT        35000               12.42               0.39   

  payment_default_on_file  credit_history_length  loan_approval_status  max_allowed_loan  
0                       N                      4                     0          -2426900  
1                       Y                      3                     0           -111739  
2                       N                      3                     0            -89000  
3                       N                     11                     0             35000  
4                       N                     14                     0             35000

In [7]:
data.describe(include='all').transpose()

count unique        top   freq     mean      std         min      25%      50%      75%        max
id                      58645.00    NaN        NaN    NaN 29322.00 16929.50        0.00 14661.00 29322.00 43983.00   58644.00
age                     58639.00    NaN        NaN    NaN    27.55     6.03       20.00    23.00    26.00    30.00     123.00
income                  58645.00    NaN        NaN    NaN 64046.17 37931.11     4200.00 42000.00 58000.00 75600.00 1900000.00
home_ownership             58645      4       RENT  30594      NaN      NaN         NaN      NaN      NaN      NaN        NaN
emplyment_length        58645.00    NaN        NaN    NaN     4.70     4.00        0.00     2.00     4.00     7.00     150.00
loan_intent                58645      6  EDUCATION  12271      NaN      NaN         NaN      NaN      NaN      NaN        NaN
loan_amount             58645.00    NaN        NaN    NaN  9217.56  5563.81      500.00  5000.00  8000.00 12000.00   35000.00
loan_interest_rate      58634.00    NaN        NaN    NaN    10.68     3.04      -11.14     7.88    10.75    12.99      23.22
loan_income_ratio       58645.00    NaN        NaN    NaN     0.16     0.09        0.00     0.09     0.14     0.21       0.83
payment_default_on_file    58640      2          N  49940      NaN      NaN         NaN      NaN      NaN      NaN        NaN
credit_history_length   58645.00    NaN        NaN    NaN     5.81     4.03        2.00     3.00     4.00     8.00      30.00
loan_approval_status    58645.00    NaN        NaN    NaN     0.14     0.35        0.00     0.00     0.00     0.00       1.00
max_allowed_loan        58645.00    NaN        NaN    NaN 69754.72 61750.91 -2426900.00 38003.00 62392.00 92716.00 2638778.00

In [8]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 58645 entries, 0 to 58644
Data columns (total 13 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   id                       58645 non-null  int64  
 1   age                      58639 non-null  float64
 2   income                   58645 non-null  int64  
 3   home_ownership           58645 non-null  object 
 4   emplyment_length         58645 non-null  int64  
 5   loan_intent              58645 non-null  object 
 6   loan_amount              58645 non-null  int64  
 7   loan_interest_rate       58634 non-null  float64
 8   loan_income_ratio        58645 non-null  float64
 9   payment_default_on_file  58640 non-null  object 
 10  credit_history_length    58645 non-null  int64  
 11  loan_approval_status     58645 non-null  int64  
 12  max_allowed_loan         58645 non-null  int64  
dtypes: float64(3), int64(7), object(3)
memory usage: 5.8+ MB


In [9]:
data.isnull().sum()

id                          0
age                         6
income                      0
home_ownership              0
emplyment_length            0
loan_intent                 0
loan_amount                 0
loan_interest_rate         11
loan_income_ratio           0
payment_default_on_file     5
credit_history_length       0
loan_approval_status        0
max_allowed_loan            0
dtype: int64

In [10]:
loan_approve_status_fig = px.histogram(data,x='loan_approval_status')
loan_max_amount_fig = px.histogram(data,x='max_allowed_loan')
loan_approve_status_fig.show()
loan_max_amount_fig.show()

In [11]:
fig = px.box(data, x="max_allowed_loan")
fig.show()


In [12]:
print('home_ownership categories are:', data['home_ownership'].unique())
print('loan_intent categories are:',data['loan_intent'].unique())
print('payment_default_on_file categories are:',data['payment_default_on_file'].unique())

home_ownership categories are: ['OWN' 'RENT' 'MORTGAGE' 'OTHER']
loan_intent categories are: ['EDUCATION' 'MEDICAL' 'HOMEIMPROVEMENT' 'VENTURE' 'DEBTCONSOLIDATION'
 'PERSONAL']
payment_default_on_file categories are: ['N' 'Y' nan]


In [13]:
def find_outliers_IQR(data):
  q1=data.quantile(0.25)
  q3=data.quantile(0.75)
  IQR=q3-q1
  outliers = data[((data<(q1-1.5*IQR)) | (data>(q3+1.5*IQR)))]
  return outliers

In [14]:
age_outliers = find_outliers_IQR(data['age'])
print("number of outliers: "+ str(len(age_outliers)))
print("max outlier value: "+ str(age_outliers.max()))
print("min outlier value: "+ str(age_outliers.min()))
age_outliers.sort_values(ascending=False)

number of outliers: 2446
max outlier value: 123.0
min outlier value: 41.0


39792   123.00
56540    84.00
54600    84.00
8728     80.00
8727     80.00
8726     76.00
25687    73.00
8725     73.00
15263    73.00
36007    70.00
51884    70.00
8723     70.00
26621    70.00
8724     70.00
49824    70.00
9607     70.00
38857    70.00
14169    70.00
8875     70.00
58162    69.00
39044    69.00
11354    69.00
55536    69.00
17443    69.00
26142    69.00
49406    66.00
27712    66.00
58328    66.00
8722     66.00
24924    66.00
15803    66.00
43316    66.00
12583    66.00
29130    66.00
49730    66.00
51042    66.00
40823    65.00
8720     65.00
15339    65.00
13576    65.00
53796    65.00
8721     65.00
28672    65.00
27284    65.00
12337    65.00
51411    65.00
47757    65.00
58013    65.00
19711    65.00
56038    64.00
24312    64.00
30651    64.00
52785    64.00
47273    64.00
58024    64.00
35800    64.00
18834    64.00
8719     64.00
47782    64.00
8718     62.00
44360    62.00
8954     62.00
18773    62.00
34006    62.00
16438    62.00
55632    62.00
23476    6

In [15]:
emplyment_length_outliers = find_outliers_IQR(data['emplyment_length'])
print("number of outliers: "+ str(len(emplyment_length_outliers)))
print("max outlier value: "+ str(emplyment_length_outliers.max()))
print("min outlier value: "+ str(emplyment_length_outliers.min()))
emplyment_length_outliers.sort_values(ascending=False)

number of outliers: 1275
max outlier value: 150
min outlier value: 15


9479     150
6008     123
56728    123
37054     41
44566     41
48831     39
37571     35
51756     31
8573      31
33088     31
53032     31
41389     31
58438     30
32426     30
32839     29
47356     29
51337     28
31650     28
8565      28
55637     28
57228     27
44360     27
28583     27
8484      27
8727      27
8135      27
42517     27
46677     26
21265     26
45423     26
57924     26
49520     26
55570     26
58458     26
48867     26
8432      26
8423      26
8342      26
57741     25
35717     25
43365     25
8394      25
212       25
51258     25
48859     25
47144     25
57956     24
58008     24
12369     24
54820     24
57955     24
78        24
42755     24
49317     24
7836      24
48346     24
50212     24
44192     24
35307     24
58232     24
8659      23
8360      23
22882     23
8674      23
58280     23
42469     23
8383      23
8255      23
44709     23
17325     23
39235     23
34743     23
8664      22
42944     22
46887     22
25787     22
54281     22

In [16]:
emplyment_length_outliers = find_outliers_IQR(data['emplyment_length'])
print("number of outliers: "+ str(len(emplyment_length_outliers)))
print("max outlier value: "+ str(emplyment_length_outliers.max()))
print("min outlier value: "+ str(emplyment_length_outliers.min()))
emplyment_length_outliers.sort_values(ascending=False)

number of outliers: 1275
max outlier value: 150
min outlier value: 15


9479     150
6008     123
56728    123
37054     41
44566     41
48831     39
37571     35
51756     31
8573      31
33088     31
53032     31
41389     31
58438     30
32426     30
32839     29
47356     29
51337     28
31650     28
8565      28
55637     28
57228     27
44360     27
28583     27
8484      27
8727      27
8135      27
42517     27
46677     26
21265     26
45423     26
57924     26
49520     26
55570     26
58458     26
48867     26
8432      26
8423      26
8342      26
57741     25
35717     25
43365     25
8394      25
212       25
51258     25
48859     25
47144     25
57956     24
58008     24
12369     24
54820     24
57955     24
78        24
42755     24
49317     24
7836      24
48346     24
50212     24
44192     24
35307     24
58232     24
8659      23
8360      23
22882     23
8674      23
58280     23
42469     23
8383      23
8255      23
44709     23
17325     23
39235     23
34743     23
8664      22
42944     22
46887     22
25787     22
54281     22

In [17]:
loan_interest_rate_outliers = find_outliers_IQR(data['loan_interest_rate'])
print("number of outliers: "+ str(len(loan_interest_rate_outliers)))
print("max outlier value: "+ str(loan_interest_rate_outliers.max()))
print("min outlier value: "+ str(loan_interest_rate_outliers.min()))
loan_interest_rate_outliers.sort_values(ascending=True)

number of outliers: 35
max outlier value: 23.22
min outlier value: -11.14


8998    -11.14
10845    20.69
50909    20.69
3198     20.69
4234     20.80
4232     20.86
2837     20.86
35364    20.89
6303     20.89
2842     20.89
37217    20.89
52991    20.89
8183     20.89
2166     21.21
4815     21.21
741      21.21
7087     21.21
7442     21.21
36613    21.36
54223    21.36
8630     21.36
727      21.36
8562     21.36
3801     21.36
2123     21.36
8627     21.36
58150    21.64
36949    21.74
47293    21.74
1969     21.74
783      21.74
46452    22.06
57238    22.11
1478     23.06
6550     23.22
Name: loan_interest_rate, dtype: float64

In [18]:
max_allowed_loan_outliers = find_outliers_IQR(data['max_allowed_loan'])
print("number of outliers: "+ str(len(max_allowed_loan_outliers)))
print("max outlier value: "+ str(max_allowed_loan_outliers.max()))
print("min outlier value: "+ str(max_allowed_loan_outliers.min()))
max_allowed_loan_outliers.sort_values(ascending=True)

number of outliers: 2233
max outlier value: 2638778
min outlier value: -2426900


0       -2426900
1        -111739
2         -89000
56415     174791
56416     174817
56417     174945
56418     174953
56419     174953
56420     174958
56421     174963
56422     174963
56423     174963
56424     174967
56425     174972
56429     174975
56428     174975
56426     174975
56427     174975
56430     174978
56431     174978
56436     174979
56432     174979
56433     174979
56434     174979
56435     174979
56437     174979
56438     174979
56439     174983
56440     174983
56441     174989
56442     175003
56443     175179
56444     175225
56445     175228
56446     175384
56447     175431
56448     175452
56449     175467
56450     175467
56451     175467
56465     175473
56464     175473
56462     175473
56461     175473
56460     175473
56459     175473
56463     175473
56457     175473
56456     175473
56455     175473
56454     175473
56458     175473
56453     175473
56452     175473
56466     175474
56467     175549
56468     175576
56469     175708
56470     1757

In [19]:
data.drop(data.index[[39792, 9479, 6008, 56728, 8998, 0, 1, 2]], inplace=True)

In [20]:
age_fig = px.box(data, x='age')
emplyment_length_fig = px.box(data, x='emplyment_length')
loan_interest_rate_fig = px.box(data, x='loan_interest_rate')
max_allowed_loan_fig = px.box(data, x='max_allowed_loan')

age_fig.show()
emplyment_length_fig.show()
loan_interest_rate_fig.show()
max_allowed_loan_fig.show()

In [21]:
label_encoder = preprocessing.LabelEncoder()

# Encode the categories in each object variable to a numeric form
data['home_ownership']= label_encoder.fit_transform(data['home_ownership'])
data['loan_intent']= label_encoder.fit_transform(data['loan_intent'])
data['payment_default_on_file']= label_encoder.fit_transform(data['payment_default_on_file'])

# Check the categories' labels after the label encoding transformation is completed
print("New labels for home_ownership are: ", data['home_ownership'].unique())
print("New labels for loan_intent are: ", data['loan_intent'].unique())
print("New labels for payment_default_on_file are: ", data['payment_default_on_file'].unique())

New labels for home_ownership are:  [3 0 2 1]
New labels for loan_intent are:  [1 2 5 0 4 3]
New labels for payment_default_on_file are:  [0 1 2]


In [22]:
# Calculate the mean of each variable
Mean_age = data['age'].mean()
Mean_loan_interest_rate = data['loan_interest_rate'].mean()

# use the mean to impute the missing values in each variable
data['age'].fillna(Mean_age, inplace=True)
data['loan_interest_rate'].fillna(Mean_loan_interest_rate, inplace=True)

In [23]:
data.isna().sum()/len(data)*100

id                        0.00
age                       0.00
income                    0.00
home_ownership            0.00
emplyment_length          0.00
loan_intent               0.00
loan_amount               0.00
loan_interest_rate        0.00
loan_income_ratio         0.00
payment_default_on_file   0.00
credit_history_length     0.00
loan_approval_status      0.00
max_allowed_loan          0.00
dtype: float64

In [24]:
data.to_csv(r'prepared_loan_approval_data.csv', index=False)